### Lecture 1: Means, Variances, and $\chi^2$

Example solution provided by Tania Kozynets (AMAS-2021 TA), Feb. 8, 2021;

see alternative solutions by [Jason](https://www.nbi.dk/~koskinen/Teaching/AdvancedMethodsInAppliedStatistics2020/Exercises/Lecture1_Variance.py) (course lecturer) and [Jean-Loup](https://www.nbi.dk/~koskinen/Teaching/AdvancedMethodsInAppliedStatistics2020/Exercises/Lecture1_Variance_Py3.ipynb) (AMAS-2019 TA).

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

### Data parsing

We will first read in the data as a [pandas DataFrame](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.html), clean it up, and find the headers for each of the five datasets.

In [2]:
#Reading in the data:
data = pd.read_table('FranksNumbers.txt.1',header=1,sep='\s+',
                    names = ['x','y_measured','to_be_dropped'])

#The last column now contains NaN values, which is why we drop it:
data = data.drop(['to_be_dropped'],axis=1)

#Next, we will check if the first symbol, data['x'][i][0], in each data row [i] is a digit.
check_if_numerical = np.array([data['x'][i][0].isdigit() for i in range(len(data))])

#If the above test was failed and the first symbol is not a digit, it must be a letter (in this case).
#This means that we found a header for the next dataset. Recording the indices of all header rows in this manner:
header_rows = np.where(check_if_numerical == False)[0]

#We will also append -1 from above, since this is technically where the 1st header belongs.
breaking_rows = np.append(-1,header_rows)
breaking_rows = np.append(breaking_rows,len(data))

#We will store the individual datasets in the dictionary below, starting with the row of the previous header
#and ending with the row of the next header.
individual_datasets = {}

for dataset_number in range(len(header_rows)+1):
    #We will also remember to change the format to float (as it used to be string before)
    individual_datasets[dataset_number+1] = \
    data[breaking_rows[dataset_number]+1:breaking_rows[dataset_number+1]].astype('float')

### Calculating the mean and the variance

Below, we define a function for calculating the variance of the given samples, using either biased (assuming _N_ DOF) or an unbiased (assuming _N-1_ DOF) estimator.

In [3]:
def calc_variance(samples,bias=False):
    N = len(samples)
    if bias:
        return np.sum((samples-np.average(samples))**2)/N
    else:
        return np.sum((samples-np.average(samples))**2)/(N-1)

In [4]:
#We will store the means and the variances as dictionaries as well, with dataset number being our key.
means = {}
unbiased_variances = {}
biased_variances = {}

for dataset_number in range(len(header_rows)+1):
    #Create placeholders to compute variances for a given column of the dataset:
    means[dataset_number+1] = {}
    unbiased_variances[dataset_number+1] = {}
    biased_variances[dataset_number+1] = {}
    
    #Loop through the columns. For us, these are "x" and "y_measured". 
    #We will only need to report the variance for the y variable in the end.
    
    for column in data.columns:
        
        #The mean calculation is done using the standard numpy.average function:
        means[dataset_number+1][column] = np.average(individual_datasets[dataset_number+1][column])
        
        #The variance calculation is done using our custom calc_variance function, with the appropriate bias flag.
        #For bias = False, one could alternatively use np.var(samples,ddof=1) as in Jason's solution.
        unbiased_variances[dataset_number+1][column] = \
        calc_variance(individual_datasets[dataset_number+1][column], bias = False)
        
        #For bias = True, one could alternatively use np.var(samples,ddof=0) as in Jason's solution.
        biased_variances[dataset_number+1][column] = \
        calc_variance(individual_datasets[dataset_number+1][column], bias = True)
        

### Calculating the $\chi^2$

Below, we define a function to calculate the $\chi^2$ given the expected data (y_expected), the observed data (y_measured) and the uncertainty on the observed data (y_err).

This can work with any form of y_err, which is why we can reuse it for either Pearson's $\chi^2$ with y_err = sqrt(y_expected) or y_err = 1.22 for all data points.

In [5]:
def chi2(y_expected,y_measured,y_err):
    return np.sum((y_expected-y_measured)**2/(y_err**2))

In [6]:
#The calculated chi2 values will be again stored as dictionaries with dataset numbers as keys.
chi2_with_sqrt_unc = {}
chi2_with_fixed_unc = {}

reduced_chi2_with_sqrt_unc = {}
reduced_chi2_with_fixed_unc = {}

#Looping through the dataset numbers:
for dataset_number in range(5):
    
    #The expected y value is calculated from the line equation provided in the lecture notes,
    #i.e. 0.48*x + 3.02. 
    y_expected = individual_datasets[dataset_number+1]['x']*0.48 + 3.02
    
    #Now, we evaluate the chi2 using the function we have defined above.
    #chi2_with_sqrt is the Pearson's chi2 with y_err = sqrt(y_measured).
    #Note that it's not necessary to pass the keywords (y_expected=..., etc) to the function; this is done
    #for purely illustrative purposes.
    chi2_with_sqrt_unc[dataset_number+1] = chi2(y_expected = y_expected,
                                           y_measured = individual_datasets[dataset_number+1]['y_measured'],
                                           y_err = np.sqrt(y_expected))
    
    #chi2_with_fixed_unc is the chi2 assuming y_err = const = 1.22
    chi2_with_fixed_unc[dataset_number+1] = chi2(y_expected = y_expected,
                                           y_measured = individual_datasets[dataset_number+1]['y_measured'],
                                           y_err = np.full_like(individual_datasets[dataset_number+1]['x'],1.22))
    
    #We can also calculate the reduced chi2 by dividing total chi2 by the number of DOF.
    #Since we are trying to "fit" a line with 2 parameters (slope and interpect), we will be dividing 
    #by the number of DOF equal to N-2 here.
    reduced_chi2_with_sqrt_unc[dataset_number+1] = chi2_with_sqrt_unc[dataset_number+1]/(len(y_expected)-2)
    reduced_chi2_with_fixed_unc[dataset_number+1] = chi2_with_fixed_unc[dataset_number+1]/(len(y_expected)-2)

### Report the results

In [7]:
for dataset_number in range(5):
    
    print("Dataset %s"%str(dataset_number+1))
    
    print("Biased variance:    {:.3f}".format(biased_variances[dataset_number+1]['y_measured']))
    print("Unbiased variance:    {:.3f}".format(unbiased_variances[dataset_number+1]['y_measured']))
    
    print("Pearson's chi-squared (w/ sqrt uncertainty):    {:.3f}".format(chi2_with_sqrt_unc[dataset_number+1]))
    print("Chi-squared (w/ ±1.22 uncertainty):    {:.3f}".format(chi2_with_fixed_unc[dataset_number+1]))

    print("Reduced Pearson's chi-squared (w/ sqrt uncertainty):    {:.3f}".format(reduced_chi2_with_sqrt_unc[dataset_number+1]))
    print("Reduced chi-squared (w/ ±1.22 uncertainty):    {:.3f}".format(reduced_chi2_with_fixed_unc[dataset_number+1]))
    print("\n")
    

Dataset 1
Biased variance:    3.752
Unbiased variance:    4.127
Pearson's chi-squared (w/ sqrt uncertainty):    1.887
Chi-squared (w/ ±1.22 uncertainty):    9.468
Reduced Pearson's chi-squared (w/ sqrt uncertainty):    0.210
Reduced chi-squared (w/ ±1.22 uncertainty):    1.052


Dataset 2
Biased variance:    3.752
Unbiased variance:    4.128
Pearson's chi-squared (w/ sqrt uncertainty):    2.072
Chi-squared (w/ ±1.22 uncertainty):    9.477
Reduced Pearson's chi-squared (w/ sqrt uncertainty):    0.230
Reduced chi-squared (w/ ±1.22 uncertainty):    1.053


Dataset 3
Biased variance:    3.748
Unbiased variance:    4.123
Pearson's chi-squared (w/ sqrt uncertainty):    1.555
Chi-squared (w/ ±1.22 uncertainty):    9.460
Reduced Pearson's chi-squared (w/ sqrt uncertainty):    0.173
Reduced chi-squared (w/ ±1.22 uncertainty):    1.051


Dataset 4
Biased variance:    3.748
Unbiased variance:    4.123
Pearson's chi-squared (w/ sqrt uncertainty):    2.043
Chi-squared (w/ ±1.22 uncertainty):    9.4